<h2> Smart Trader </h2>

In [ ]:
#reference text
#https://books.google.com.sg/books?id=HnetDwAAQBAJ&pg=PT710&lpg=PT710&dq=replay+buffer+keras&source=bl&ots=kOYzzExOB5&sig=ACfU3U3A3YbvM4DuqReHvK1aYEtiDIpKUQ&hl=en&sa=X&ved=2ahUKEwiLtoHTk6zpAhXbeisKHUpCDkoQ6AEwA3oECAgQAQ#v=onepage&q=replay%20buffer%20keras&f=false
#https://towardsdatascience.com/how-to-train-your-quadcopter-adventures-in-machine-learning-algorithms-e6ee5033fd61
#https://towardsdatascience.com/understanding-and-implementing-distributed-prioritized-experience-replay-horgan-et-al-2018-d2c1640e0520
#https://github.com/PacktPublishing/Python-Reinforcement-Learning-Projects
#https://github.com/germain-hug/Deep-RL-Keras

In [1]:
from keras import layers, models, optimizers,regularizers,initializers
from keras import backend as K
import numpy as np
import pandas as pd
from numpy.random import choice
import random
from collections import namedtuple, deque
import math

Using TensorFlow backend.
C:\Users\meiro\anaconda3\envs\python3\lib\site-packages\tensorflow\python\framework\dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\meiro\anaconda3\envs\python3\lib\site-packages\tensorflow\python\framework\dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\meiro\anaconda3\envs\python3\lib\site-packages\tensorflow\python\framework\dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\meiro\anaconda3\envs\python3\lib

<h4> Actor Network</h4> 
<p> Purpose: Define the actor (policy) model.The actor could be a neural network taking observations (states) as inputs and outputting one possible action. </p>
<p> Possible Improvements: Policy Search Improvement: When the policy space is big,finding a good set of parameters via brute force search is diffcult, in that case genetic algorithm can be used for more efficient policy search. Example: create a first generation of 100 random policies, evaluate their performance and remove 80 bad policies.Then make the surviving policies to cross-over and mutate to produce the second generation. Then the process iterates until an acceptable solution is found. </p>

In [2]:
#the aim of the training is to maximise the discounted accumulative rewards & minimise the negatives of Q-value
#could switch the model to keras sequential model
class Actor:
    def __init__(self, state_size, action_size):
        self. state_size = state_size
        self. action_size = action_size
        self. build_model()
    
    def build_model(self):
        #add states as the inputs
        states = layers.Input(shape=(self.state_size,), name='states')
        #dimensionality of the first output space=16 (16 neurons)
        net = layers.Dense(units=16,kernel_regularizer=regularizers.l2(1e-6))(states) 
        net = layers.BatchNormalization()(net) #Normalize and scale inputs which allows each layer of a network to learn by itself a little bit more independently of other layers
        net = layers.Activation("relu")(net)
        #dimensionality of the second output space= 32 (32 neurons)
        net = layers.Dense(units=32,kernel_regularizer=regularizers.l2(1e-6))(net)
        net = layers.BatchNormalization()(net)
        net = layers.Activation("relu")(net)  
        #dimensionality of the third output space= number of possible actions, each action is predicted with an probability
        actions = layers.Dense(units=self.action_size, activation='softmax', name = 'actions')(net)
        #the models class groups layers into an object with training and inference features.
        self.model = models.Model(inputs=states, outputs=actions)
        #model.save('data/actor_model')
        #define the loss function by using the action value (Q_value) gradients, for policy evaluation 
        action_gradients = layers.Input(shape=(self.action_size,))
        loss = K.mean(-action_gradients * actions) #the aims is to minimise the negatives of Q-values
        #define the optimizer and train the function
        optimizer = optimizers.Adam(lr=.00001)
        updates_op = optimizer.get_updates(params=self.model.trainable_weights, loss=loss)
        self.train_fn = K.function(inputs=[self.model.input, action_gradients, K.learning_phase()],outputs=[],updates=updates_op)


<h4> Critic Network </h4>
<p> Purpose: Build a critic (value) network that maps state and action pairs
(Q_values) </p>

In [3]:
class Critic:
    def __init__(self, state_size, action_size):
        self.state_size = state_size
        self.action_size = action_size
        self.build_model()

    def build_model(self):
        states = layers.Input(shape=(self.state_size,), name='states')
        actions = layers.Input(shape=(self.action_size,), name='actions')
        net_states = layers.Dense(units=16,kernel_regularizer=regularizers.l2(1e-6))(states)
        net_states = layers.BatchNormalization()(net_states)
        net_states = layers.Activation("relu")(net_states)
        #two inputs dense to same shapes
        net_states = layers.Dense(units=32, kernel_regularizer=regularizers.l2(1e-6))(net_states)
        net_actions = layers.Dense(units=32,kernel_regularizer=regularizers.l2(1e-6))(actions)
        #add the two inputs
        net = layers.Add()([net_states, net_actions])
        net = layers.Activation('relu')(net)
        #the final output layer will produce the Q-value
        Q_values = layers.Dense(units=1, name='q_values',kernel_initializer=initializers.RandomUniform(minval=-0.003, maxval=0.003))(net)
        self.model = models.Model(inputs=[states, actions], outputs=Q_values)
        optimizer = optimizers.Adam(lr=0.001)
        self.model.compile(optimizer=optimizer, loss='mse')
        action_gradients = K.gradients(Q_values, actions)
        self.get_action_gradients = K.function(inputs=[*self.model.input, K.learning_phase()],outputs=action_gradients)

<h4> Agent </h4>
<p> Purpose: define an agent to train the actor and critic </p>

In [4]:
'''instead of training the DQN on the latest experiences, we will store all experiences in a replay buffer
   or a replay memory and we will sample a random training from it at each training iteration. This helps to reduce
   the correlation between the experiences in a training batch, which tremendously help training.
'''
# prioritized Experience Replay /importance sampling (sample important experiences more frequently)
#https://towardsdatascience.com/understanding-and-implementing-distributed-prioritized-experience-replay-horgan-et-al-2018-d2c1640e0520

class ReplayBuffer:
    def __init__(self, buffer_size, batch_size):
        self.memory = deque(maxlen=buffer_size)
        self.batch_size = batch_size
        self.experience = namedtuple("Experience", field_names=["state", "action", "reward", "next_state", "done"])
    #Add a new experience to the replay buffer memory
    def add(self, state, action, reward, next_state, done):
        e = self.experience(state, action, reward, next_state, done)
        self.memory.append(e)
    # randomly sample states from a memory buffer to improve overfitting
    def sample(self, batch_size=32):
        return random.sample(self.memory, k=self.batch_size)
    #Return the current size of the buffer memory
    def __len__(self):
        return len(self.memory)

<p>Possible Improvements: Policy Gradient </p>

In [5]:
#learns via actor and agent networks
class Agent:
    def __init__(self, state_size, batch_size, is_eval = False):
        #replay memory size
        self.state_size = state_size
        self.action_size = 3 #3 actions: buy, sell, hold
        self.buffer_size = 1000000
        self.batch_size = batch_size
        self.memory = ReplayBuffer(self.buffer_size, self.batch_size)
        self.inventory = []
        #whether or not training is ongoing. This variable will be changed during the training and evaluation phase
        self.is_eval = is_eval 
        #discount factor in Bellman equation
        self.gamma = 0.99
        #a soft update of the actor and critic networks
        self.tau = 0.001
        #the actor policy model maps states to actions
        self.actor_local = Actor(self.state_size, self.action_size)
        self.actor_target = Actor(self.state_size, self.action_size)
        self.actor_target.model.set_weights(self.actor_local.model.get_weights()) #sets the target model parameters to local model parameters
        #the critic (value) model  maps the state-action pairs to Q_values 
        self.critic_local = Critic(self.state_size, self.action_size)
        self.critic_target = Critic(self.state_size, self.action_size)
        self.critic_target.model.set_weights(self.critic_local.model.get_weights()) 
    
    #the function will return the actions with probability distributions, given a state, using the actor (policy) network
    #the action with highest probability is the best action given the state
    def act(self, state):
        options = self.actor_local.model.predict(state)
        self.last_state = state
        if not self.is_eval:
            return choice(range(3), p = options[0])
        return np.argmax(options[0])
    
    #the function will assign a stochastic policy, based on the action probabilities in the training model
    #the function will assign a deterministic action corresponding to the maximum probability in the testing model
    #the function will return the set of actions carried by the agent in each episode (all steps are recorded)
    def step(self, action, reward, next_state, done):
        self.memory.add(self.last_state, action, reward, next_state, done) #adds a new experience to the memory
        if len(self.memory) > self.batch_size: #when enough experiences are presented in memory for training 
            experiences = self.memory.sample(self.batch_size)# a ranfom sample will be pulled for training 
            self.learn(experiences) #the agent then learns from the sample experience
            self.last_state = next_state #update the state to next state
    
    #the function will learned the sampled experiences through the actor and the critic
    def learn(self, experiences):               
        states = np.vstack([e.state for e in experiences if e is not None]).astype(np.float32).reshape(-1,self.state_size)    
        actions = np.vstack([e.action for e in experiences if e is not None]).astype(np.float32).reshape(-1,self.action_size)
        rewards = np.array([e.reward for e in experiences if e is not None]).astype(np.float32).reshape(-1,1)
        dones = np.array([e.done for e in experiences if e is not None]).astype(np.float32).reshape(-1,1)
        next_states = np.vstack([e.next_state for e in experiences if e is not None]).astype(np.float32).reshape(-1,self.state_size)

        actions_next = self.actor_target.model.predict_on_batch(next_states)
        Q_targets_next = self.critic_target.model.predict_on_batch([next_states, actions_next])
        
        Q_targets = rewards + self.gamma * Q_targets_next * (1 - dones)
        self.critic_local.model.train_on_batch(x = [states, actions], y=Q_targets)
        
        action_gradients = np.reshape(self.critic_local.get_action_gradients([states, actions, 0]),(-1, self.action_size))
        self.actor_local.train_fn([states, action_gradients, 1])
        self.soft_update(self.critic_local.model, self.critic_target.model)  
        self.soft_update(self.actor_local.model, self.actor_target.model)
    
    #the function performs soft updates on the model parameters to avoid drastic model changes
    def soft_update(self, local_model, target_model):
        local_weights = np.array(local_model.get_weights())
        target_weights = np.array(target_model.get_weights())

        assert len(local_weights) == len(target_weights)

        new_weights = self.tau * local_weights + (1 - self.tau) * target_weights
        target_model.set_weights(new_weights)


<h4> Visualisation </h4>

In [15]:
import numpy as np
import math


def formatPrice(n):
    if n >= 0:
        curr = "$"
    else:
        curr = "-$"
    return curr + "{0:.2f}".format(abs(n))


def getStockData(key):
    datavec = []
    lines = open("data/" + key + ".csv", "r").read().splitlines()
    
    for line in lines[1:]:
        datavec.append(float(line.split(",")[4]))
    
    return datavec
  

def getState(data, t, window):
    if t - window >= -1:
        vec = data[t - window + 1:t + 1]
    else: 
        vec = -(t-window+1)*[data[0]]+data[0: t + 1]
    scaled_state = []
    for i in range(window - 1):
        scaled_state.append(1/(1 + math.exp(vec[i] - vec[i+1])))
    
    return np.array([scaled_state])

<h4> Train and Test </h4>

In [11]:
train_path = 'data\SPY_training.csv'
test_path = 'data\SPY_test.csv'

In [12]:
train_df = pd.read_csv(train_path)
train_df.head(5)

Date      Open      High       Low     Close  Adj Close   Volume
0  1993-01-29  43.96875  43.96875  43.75000  43.93750  26.299288  1003200
1  1993-02-01  43.96875  44.25000  43.96875  44.25000  26.486324   480500
2  1993-02-02  44.21875  44.37500  44.12500  44.34375  26.542448   201300
3  1993-02-03  44.40625  44.84375  44.37500  44.81250  26.822998   529400
4  1993-02-04  44.96875  45.09375  44.46875  45.00000  26.935240   531500

In [13]:
test_df = pd.read_csv(test_path)
test_df.head(5)

Date        Open        High         Low       Close   Adj Close  \
0  2019-01-02  245.979996  251.210007  245.949997  250.179993  244.095322   
1  2019-01-03  248.229996  248.570007  243.669998  244.210007  238.270538   
2  2019-01-04  247.589996  253.110001  247.169998  252.389999  246.251556   
3  2019-01-07  252.690002  255.949997  251.690002  254.380005  248.193176   
4  2019-01-08  256.820007  257.309998  254.000000  256.769989  250.525040   

      Volume  
0  126925200  
1  144140700  
2  142628800  
3  103139100  
4  102512600

In [ ]:
window_size = 50
batch_size = 32
agent = Agent(window_size, batch_size)
data = getStockData("SPY_training")
#data = train_df
l = len(data) - 1
episode_count = 300

for e in range(episode_count):
    print("Episode " + str(e) + "/" + str(episode_count))
    state = getState(data, 0, window_size + 1)

    agent.inventory = []
    total_profit = 0
    done = False
    for t in range(l):
        action = agent.act(state)
        action_prob = agent.actor_local.model.predict(state)

        next_state = getState(data, t + 1, window_size + 1)
        reward = 0

        if action == 1:
            agent.inventory.append(data[t])
            print("Buy:" + formatPrice(data[t]))

        elif action == 2 and len(agent.inventory) > 0:
            bought_price = agent.inventory.pop(0)
            reward = max(data[t] - bought_price, 0)
            total_profit += data[t] - bought_price
            print("sell: " + formatPrice(data[t]) + "| profit: " + formatPrice(data[t] - bought_price))

        if t == l - 1:
            done = True
        agent.step(action_prob, reward, next_state, done)
        state = next_state

        if done:
            print("------------------------------------------")
            print("Total Profit: " + formatPrice(total_profit))
            print("------------------------------------------")

test_data = getStockData("SPY_training")
#test_data = test_df
l_test = len(test_data) - 1
state = getState(test_data, 0, window_size + 1)
total_profit = 0
agent.inventory = []
agent.is_eval = False
done = False
for t in range(l_test):
    action = agent.act(state)
    next_state = getState(test_data, t + 1, window_size + 1)
    reward = 0

    if action == 1:

        agent.inventory.append(test_data[t])
        print("Buy: " + formatPrice(test_data[t]))

    elif action == 2 and len(agent.inventory) > 0:
        bought_price = agent.inventory.pop(0)
        reward = max(test_data[t] - bought_price, 0)
        total_profit += test_data[t] - bought_price
        print("Sell: " + formatPrice(test_data[t]) + " | profit: " + formatPrice(test_data[t] - bought_price))

    if t == l_test - 1:
        done = True
    agent.step(action_prob, reward, next_state, done)
    state = next_state

    if done:
        print("------------------------------------------")
        print("Total Profit: " + formatPrice(total_profit))
        print("------------------------------------------")


Episode 0/300
Buy:$43.94
Buy:$44.25
sell: $44.81| profit: $0.88
sell: $45.00| profit: $0.75
Buy:$44.97
sell: $44.72| profit: -$0.25
Buy:$43.47
sell: $43.56| profit: $0.09
Buy:$44.41
sell: $44.28| profit: -$0.12
Buy:$44.94
Buy:$45.12
Buy:$44.75
Buy:$45.59
Buy:$45.09
sell: $45.31| profit: $0.38
Buy:$45.03
Buy:$45.31
Buy:$45.03
Buy:$44.88
sell: $45.16| profit: $0.03
sell: $44.91| profit: $0.16
sell: $45.09| profit: -$0.50
sell: $45.22| profit: $0.12
Buy:$44.09
sell: $44.19| profit: -$0.84
sell: $44.28| profit: -$1.03
sell: $45.00| profit: -$0.03
sell: $44.94| profit: $0.06
sell: $44.94| profit: $0.84
Buy:$43.41
sell: $43.88| profit: $0.47
Buy:$44.31
sell: $44.47| profit: $0.16
Buy:$44.59
Buy:$44.44
sell: $44.62| profit: $0.03
sell: $44.56| profit: $0.12
Buy:$44.00
sell: $44.16| profit: $0.16
Buy:$45.16
Buy:$44.75
Buy:$44.94
Buy:$45.44
Buy:$45.66
Buy:$45.59
Buy:$45.44
sell: $45.28| profit: $0.12
sell: $45.12| profit: $0.38
Buy:$44.72
Buy:$44.88
sell: $45.09| profit: $0.16
sell: $45.03| pro

sell: $55.92| profit: -$0.27
Buy:$55.98
Buy:$56.30
sell: $56.23| profit: -$0.06
Buy:$56.36
Buy:$56.41
Buy:$56.66
Buy:$57.19
Buy:$57.55
Buy:$57.70
sell: $58.23| profit: $2.08
sell: $58.77| profit: $2.66
sell: $58.44| profit: $2.28
sell: $58.22| profit: $2.17
sell: $58.50| profit: $2.39
sell: $58.31| profit: $2.19
Buy:$58.20
sell: $58.16| profit: $2.17
sell: $58.48| profit: $2.19
sell: $58.19| profit: $1.83
sell: $58.19| profit: $1.78
Buy:$58.36
Buy:$58.41
Buy:$57.92
sell: $57.89| profit: $1.23
Buy:$58.08
sell: $58.44| profit: $1.25
Buy:$58.62
Buy:$58.34
Buy:$58.73
Buy:$58.91
Buy:$59.19
Buy:$58.83
sell: $58.77| profit: $1.22
Buy:$57.75
sell: $58.56| profit: $0.86
sell: $58.78| profit: $0.58
Buy:$59.03
sell: $59.53| profit: $1.17
sell: $59.08| profit: $0.67
sell: $59.67| profit: $1.75
Buy:$60.19
sell: $59.88| profit: $1.80
sell: $60.36| profit: $1.73
sell: $60.17| profit: $1.83
Buy:$60.34
sell: $61.05| profit: $2.31
Buy:$60.91
Buy:$61.73
sell: $62.28| profit: $3.38
Buy:$61.95
sell: $62.16

sell: $109.56| profit: $3.00
Buy:$109.94
sell: $112.59| profit: $5.50
sell: $110.94| profit: $2.38
sell: $110.31| profit: $1.06
sell: $111.19| profit: $1.25
Buy:$110.88
sell: $112.12| profit: $1.25
Buy:$112.78
Buy:$113.09
sell: $112.00| profit: -$0.78
Buy:$110.81
sell: $108.72| profit: -$4.38
Buy:$108.56
sell: $109.31| profit: -$1.50
sell: $111.34| profit: $2.78
Buy:$110.22
sell: $109.34| profit: -$0.88
Buy:$111.94
sell: $112.22| profit: $0.28
Buy:$111.66
Buy:$111.34
sell: $112.41| profit: $0.75
Buy:$109.62
Buy:$110.12
Buy:$109.03
sell: $109.62| profit: -$1.72
sell: $112.00| profit: $2.38
sell: $111.88| profit: $1.75
sell: $112.22| profit: $3.19
Buy:$109.41
sell: $110.44| profit: $1.03
Buy:$110.06
Buy:$110.59
Buy:$111.91
sell: $113.22| profit: $3.16
sell: $113.31| profit: $2.72
sell: $114.84| profit: $2.94
Buy:$115.78
sell: $116.62| profit: $0.84
Buy:$116.50
sell: $117.81| profit: $1.31
Buy:$117.59
sell: $118.41| profit: $0.81
Buy:$116.50
sell: $114.09| profit: -$2.41
Buy:$112.53
Buy:$

Buy:$111.12
sell: $114.48| profit: -$0.53
sell: $115.94| profit: $1.74
sell: $118.31| profit: $7.19
Buy:$115.48
sell: $114.20| profit: -$1.28
Buy:$110.39
Buy:$110.85
Buy:$115.05
Buy:$113.30
sell: $114.56| profit: $4.17
sell: $116.65| profit: $5.80
Buy:$116.73
sell: $118.85| profit: $3.80
sell: $117.60| profit: $4.30
sell: $119.26| profit: $2.53
Buy:$125.65
sell: $122.24| profit: -$3.41
Buy:$125.78
sell: $126.66| profit: $0.88
Buy:$126.24
Buy:$125.65
Buy:$126.02
sell: $125.15| profit: -$1.09
Buy:$125.98
Buy:$128.95
Buy:$129.15
sell: $131.65| profit: $6.00
sell: $131.48| profit: $5.46
Buy:$129.25
Buy:$129.63
Buy:$127.08
sell: $125.30| profit: -$0.68
sell: $125.95| profit: -$3.00
Buy:$126.73
Buy:$127.34
sell: $128.80| profit: -$0.35
sell: $128.19| profit: -$1.06
sell: $127.00| profit: -$2.63
sell: $126.10| profit: -$0.98
Buy:$125.88
Buy:$122.00
Buy:$121.85
Buy:$121.26
sell: $121.79| profit: -$4.94
Buy:$122.43
sell: $123.82| profit: -$3.52
Buy:$121.72
sell: $121.55| profit: -$4.33
Buy:$122

Buy:$108.16
sell: $108.50| profit: $0.34
Buy:$108.90
Buy:$109.66
sell: $109.62| profit: $0.72
sell: $109.70| profit: $0.04
Buy:$111.16
Buy:$111.18
Buy:$111.28
sell: $111.23| profit: $0.07
Buy:$112.44
sell: $112.55| profit: $1.37
Buy:$112.93
sell: $113.38| profit: $2.10
Buy:$112.39
sell: $113.22| profit: $0.78
sell: $112.56| profit: -$0.37
sell: $113.50| profit: $1.11
Buy:$114.20
Buy:$114.80
sell: $114.43| profit: $0.23
Buy:$115.87
sell: $113.37| profit: -$1.43
Buy:$113.48
Buy:$113.48
Buy:$113.97
Buy:$113.78
sell: $113.18| profit: -$2.69
Buy:$114.45
sell: $114.48| profit: $1.00
sell: $115.65| profit: $2.17
Buy:$115.13
Buy:$115.66
sell: $115.23| profit: $1.26
sell: $114.88| profit: $1.10
Buy:$114.59
Buy:$114.39
Buy:$114.87
Buy:$115.02
sell: $116.16| profit: $1.71
Buy:$115.48
sell: $115.69| profit: $0.56
Buy:$114.96
Buy:$112.58
sell: $111.12| profit: -$4.54
sell: $112.58| profit: -$2.01
sell: $111.20| profit: -$3.19
Buy:$111.79
sell: $113.04| profit: -$1.83
sell: $113.07| profit: -$1.95
B

...

Buy:$123.31
sell: $123.31| profit: $0.00
Buy:$136.31
sell: $135.44| profit: -$0.88
Buy:$133.98
sell: $135.00| profit: $1.02
Buy:$135.75
sell: $134.75| profit: -$1.00
Buy:$130.38
sell: $130.09| profit: -$0.28
Buy:$132.06
sell: $133.69| profit: $1.62
Buy:$130.75
sell: $130.61| profit: -$0.14
Buy:$128.16
sell: $124.88| profit: -$3.28
Buy:$139.75
sell: $140.08| profit: $0.33
Buy:$143.06
sell: $145.00| profit: $1.94
Buy:$138.69
sell: $139.50| profit: $0.81
Buy:$151.25
sell: $150.12| profit: -$1.12
Buy:$144.88
sell: $147.59| profit: $2.72
Buy:$147.84
sell: $148.16| profit: $0.31
Buy:$148.69
sell: $147.44| profit: -$1.25
Buy:$143.16
sell: $145.00| profit: $1.84
Buy:$140.00
sell: $137.69| profit: -$2.31
Buy:$134.25
sell: $139.31| profit: $5.06
Buy:$132.00
sell: $132.84| profit: $0.84
Buy:$117.83
sell: $115.82| profit: -$2.01
Buy:$113.42
sell: $113.70| profit: $0.28
Buy:$107.65
Buy:$107.42
sell: $107.35| profit: -$0.30
sell: $109.47| profit: $2.05
Buy:$109.25
sell: $110.68| profit: $1.43
Buy:$1

Buy:$78.38
sell: $78.44| profit: $0.06
Buy:$92.06
sell: $91.12| profit: -$0.94
Buy:$96.97
sell: $97.00| profit: $0.03
Buy:$96.84
sell: $94.94| profit: -$1.91
Buy:$97.88
sell: $96.94| profit: -$0.94
Buy:$112.00
sell: $111.88| profit: -$0.12
Buy:$118.56
sell: $116.50| profit: -$2.06
Buy:$107.00
sell: $106.81| profit: -$0.19
Buy:$123.22
sell: $122.69| profit: -$0.53
Buy:$129.34
sell: $132.41| profit: $3.06
Buy:$136.75
sell: $137.34| profit: $0.59
Buy:$134.09
sell: $133.34| profit: -$0.75
Buy:$141.50
sell: $142.12| profit: $0.62
Buy:$142.59
sell: $142.38| profit: -$0.22
Buy:$151.22
sell: $148.69| profit: -$2.53
Buy:$143.38
sell: $141.12| profit: -$2.25
Buy:$149.12
sell: $149.78| profit: $0.66
Buy:$144.19
sell: $141.06| profit: -$3.12
Buy:$134.25
sell: $139.31| profit: $5.06
Buy:$116.69
sell: $114.20| profit: -$2.49
Buy:$120.35
sell: $120.81| profit: $0.46
Buy:$118.24
sell: $118.65| profit: $0.41
Buy:$105.80
sell: $108.51| profit: $2.71
Buy:$112.25
sell: $112.60| profit: $0.35
Buy:$115.77
s

Buy:$133.36
sell: $134.92| profit: $1.56
Buy:$136.28
sell: $136.63| profit: $0.35
Buy:$140.54
sell: $141.19| profit: $0.65
Buy:$144.89
sell: $145.21| profit: $0.32
Buy:$144.66
sell: $145.32| profit: $0.66
Buy:$148.12
sell: $149.48| profit: $1.36
Buy:$147.60
sell: $143.80| profit: -$3.80
Buy:$153.62
sell: $154.13| profit: $0.51
Buy:$150.94
sell: $150.91| profit: -$0.03
Buy:$145.88
sell: $145.88| profit: $0.00
Buy:$138.32
sell: $139.60| profit: $1.28
Buy:$141.12
sell: $141.51| profit: $0.39
Buy:$138.66
sell: $139.30| profit: $0.64
Buy:$116.06
sell: $111.85| profit: -$4.21
Buy:$88.50
sell: $101.35| profit: $12.85
Buy:$93.77
sell: $93.21| profit: -$0.56
Buy:$96.83
sell: $97.11| profit: $0.28
Buy:$92.63
sell: $89.77| profit: -$2.86
Buy:$87.16
sell: $86.91| profit: -$0.25
Buy:$107.46
sell: $109.31| profit: $1.85
Buy:$110.64
sell: $111.11| profit: $0.47
Buy:$111.95
sell: $112.48| profit: $0.53
Buy:$111.14
sell: $111.16| profit: $0.02
Buy:$116.58
sell: $117.32| profit: $0.74
Buy:$116.82
sell: 

Buy:$46.12
sell: $46.16| profit: $0.03
Buy:$46.84
sell: $46.84| profit: $0.00
Buy:$47.09
sell: $47.03| profit: -$0.06
Buy:$49.27
sell: $49.22| profit: -$0.05
Buy:$64.39
sell: $64.14| profit: -$0.25
Buy:$65.44
sell: $65.39| profit: -$0.05
Buy:$81.19
sell: $81.88| profit: $0.69
Buy:$80.59
sell: $80.12| profit: -$0.47
Buy:$91.12
sell: $92.08| profit: $0.95
Buy:$93.73
sell: $93.66| profit: -$0.08
Buy:$97.50
sell: $97.16| profit: -$0.34
Buy:$114.22
sell: $111.78| profit: -$2.44
Buy:$101.69
sell: $103.44| profit: $1.75
Buy:$126.91
sell: $126.12| profit: -$0.78
Buy:$130.81
sell: $133.31| profit: $2.50
Buy:$133.66
sell: $131.59| profit: -$2.06
Buy:$150.09
sell: $152.66| profit: $2.56
Buy:$142.25
sell: $148.16| profit: $5.91
Buy:$140.75
sell: $141.81| profit: $1.06
Buy:$137.84
sell: $138.00| profit: $0.16
Buy:$144.19
sell: $145.28| profit: $1.09
Buy:$143.00
sell: $143.88| profit: $0.88
Buy:$144.89
sell: $142.69| profit: -$2.20
Buy:$115.48
sell: $116.69| profit: $1.21
Buy:$107.39
sell: $106.86| 

Buy:$169.11
sell: $168.59| profit: -$0.52
Buy:$186.13
sell: $186.39| profit: $0.26
Buy:$195.88
sell: $194.70| profit: -$1.18
Buy:$209.38
sell: $210.07| profit: $0.69
Buy:$214.92
sell: $216.12| profit: $1.20
Buy:$247.87
sell: $247.26| profit: -$0.61
Buy:$269.50
sell: $272.02| profit: $2.52
Buy:$278.56
sell: $278.92| profit: $0.36
------------------------------------------
Total Profit: $12.41
------------------------------------------
Episode 87/300
Buy:$56.16
sell: $56.06| profit: -$0.09
Buy:$66.12
sell: $65.94| profit: -$0.19
Buy:$66.34
sell: $66.64| profit: $0.30
Buy:$66.41
sell: $66.88| profit: $0.47
Buy:$77.00
sell: $75.38| profit: -$1.62
Buy:$123.72
sell: $124.25| profit: $0.53
Buy:$130.75
sell: $130.62| profit: -$0.12
Buy:$137.72
sell: $138.50| profit: $0.78
Buy:$142.62
sell: $142.50| profit: -$0.12
Buy:$122.60
sell: $124.13| profit: $1.53
Buy:$121.19
sell: $122.24| profit: $1.05
Buy:$106.73
sell: $107.93| profit: $1.20
Buy:$110.95
sell: $111.46| profit: $0.51
Buy:$121.23
sell: $